In [1]:
#importing appropriate packages. Star is class from star.py used to create particle objects
import matplotlib.pyplot as plt
import numpy as np
from star import Star
from tqdm import tqdm

%matplotlib qt

In [2]:
#Animation import used to initialize animations
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Galaxy Mergers', artist='Cuong Bui',comment='Merging Galaxies via Toomre-Toomre')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [3]:
#Global condition
G = 1

t = 0
P = np.sqrt((4*(np.pi**2)/(1*(1e4+1e7)))*(20**3))
dt   = P/1000
tMax = P/5
n    = tMax / dt

In [4]:
n

199.99999999999997

In [5]:
'''
ODE of Keplerian orbits provided a star and a list of all the other stars.
Add_factor used to add subsqeuent terms in RK4 (used for f2-f4)
'''

def KeplerODE(dt, star, other_stars, add_factor = None):
    if add_factor == "f1":
        v = (star.f1[2:4]*dt/2.0)+star.vel
        a = 0
        for i in other_stars:
            if i.mass > 0:
                a += star.accGravGiven(i,dt,factor = "f1")
        
    elif add_factor == "f2":
        v = (star.f2[2:4]*dt/2.0)+star.vel
        a = 0
        for i in other_stars:
            if i.mass > 0:
                a += star.accGravGiven(i,dt,factor = "f2")
                
    elif add_factor == "f3":
        v = (star.f3[2:4]*dt)+star.vel
        a = 0
        for i in other_stars:
            if i.mass > 0:
                a += star.accGravGiven(i,dt,factor = "f3")
    
    else:
        v = star.vel
        a = 0
        for i in other_stars:
            if i.mass > 0:
                a += star.accGravGiven(i, dt)
            
            
    drdt = v    
    dvdt = a
    return np.concatenate((drdt,dvdt))

In [6]:
"""
General n-body dynamic simulation. Takes in a list of stars and runs 
orbital calculations for all the stars via RK4. Takes about 10 minutes for a simulation 
with 100 bodies and 40 minutes for a simulation with 200 bodies
"""
def orbit_dynamics(t, maxT, dt, star_list):
    nstars = len(star_list)
    it = int(maxT/dt)
    for iteration in tqdm(range(it)):
        for i in range(nstars):
            other_stars_list = np.delete(star_list, i)
            f1 = KeplerODE(dt    , star_list[i], other_stars_list)
            star_list[i].f1 = f1
            
        for i in range(nstars):
            other_stars_list = np.delete(star_list, i)
            f2 = KeplerODE(dt, star_list[i], other_stars_list, add_factor = "f1")
            star_list[i].f2 = f2
            
        for i in range(nstars):
            other_stars_list = np.delete(star_list, i)
            f3 = KeplerODE(dt, star_list[i], other_stars_list, add_factor = "f2")
            star_list[i].f3 = f3
            
        for i in range(nstars):
            other_stars_list = np.delete(star_list, i)
            f4 = KeplerODE(dt, star_list[i], other_stars_list, add_factor = "f3")
            star_list[i].f4 = f4
            
        for i in range(nstars):
            y_arr = (star_list[i].f1 + 2.0*star_list[i].f2 + 2.0*star_list[i].f3 + star_list[i].f4) / 6.0 * dt
            new_pos = star_list[i].pos+y_arr[:2]
            new_vel = star_list[i].vel+y_arr[2:4]
            star_list[i].save(dt, new_pos, new_vel)

        t += dt

In [7]:
#Provided a value of 1 or -1
def coin_flip():
    val = np.random.uniform()
    if val >= .5:
        return 1
    if val < .5: 
        return -1

In [8]:
'''
Creates a galaxy with n number of stars. Returns a list of Star objects.
'''
def galaxy_generator(g_mass, init_x, init_y, init_vx, init_vy, n_bodies = 100, radius = 5, c_rot = False):
    
    galactic_center = Star(g_mass, np.array([init_x, init_y, init_vx, init_vy]))
    galaxy = [galactic_center]
    
    for i in range(n_bodies):
        m = 1
        x = radius + 1
        y = radius + 1
        while (x**2) + (y**2) > radius**2:
            x = np.random.uniform(1,radius) * coin_flip()
            y = np.random.uniform(1,radius) * coin_flip()
        r = np.array([x,y])

        R = np.sqrt(sum(r**2))
        mu = (galactic_center.mass*m)/(galactic_center.mass+m)
        g_f = (G*galactic_center.mass*m)/(R**2)
        wp = np.sqrt(g_f/(mu*R))
        
        direction = np.array([1,1])
        #Clockwise vs. counterclockwise rotation
        if c_rot:  
            if r[1]+init_y < galactic_center.getXY()[1][0]: 
                direction[0] = -1
            if r[0]+init_x > galactic_center.getXY()[0][0]:
                direction[1] = -1
        else:
            if r[1]+init_y > galactic_center.getXY()[1][0]: 
                direction[0] = -1
            if r[0]+init_x < galactic_center.getXY()[0][0]:
                direction[1] = -1        

        v = (np.flip(wp*(abs(r)))*direction) + np.array([init_vx, init_vy])
        r += np.array([init_x, init_y])
        galaxy.append(Star(m, np.concatenate((r,v))))
    return galaxy

In [9]:
#Animation Function: animation_name = string
def animator(animation_name, model_list, limits = 70, axis_off = True):
    fig = plt.figure(dpi = 150)
    with writer.saving(fig, f"{animation_name}.mp4", dpi=150):
        for i in tqdm(range(np.shape(model_list[0].getXY())[1])):
            plt.clf()
            x =[]
            y = []
            for j in model_list:
                if j.mass > 1:
                    plt.plot(j.getXY()[0][i],j.getXY()[1][i], ls = "", marker = "o", ms = 6, color = "k")
                else:
                    x.append(j.getXY()[0][i])
                    y.append(j.getXY()[1][i])
            plt.plot(x,y, ls = "", marker = "o", ms = 3, color = "k", fillstyle = "none")
            plt.gca().set_ylim(-limits,limits)
            plt.gca().set_xlim(-limits,limits)
            if axis_off:
                plt.gca().set_axis_off()
            plt.draw()
            plt.pause(0.0001)
            writer.grab_frame()

## Stationary Toy Galaxy with 100 Particles

In [11]:
test_galaxy = galaxy_generator(1e7, 0, 0, 0, 0, n_bodies = 100, radius = 6, c_rot = False)
orbit_dynamics(t, tMax, dt, test_galaxy)
animator("test_galaxy_v1", test_galaxy, limits = 10)

## Moving Toy Galaxy with 100 Particles

In [12]:
test_galaxy2 = galaxy_generator(1e7, 0, -90.0, 0, 1300, n_bodies = 100, radius = 6, c_rot = False)
orbit_dynamics(t, tMax, dt, test_galaxy2)
animator("test_moving_galaxy_v1", test_galaxy2, limits = 100)

## Galaxy Trajectory

In [13]:
galaxy1 = galaxy_generator(1e7,   7,   10.0,  -360,  0, n_bodies = 0, radius = 6, c_rot = False)
galaxy2 = galaxy_generator(1e7,  -7,   -10.0,  360,  0, n_bodies = 0, radius = 6, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("galactic_center_dynamics_v1", model, limits = 20, axis_off = False)

In [14]:
galaxy1 = galaxy_generator(1e7,     11,    4.0,  -360,  0, n_bodies = 0, radius = 6, c_rot = False)
galaxy2 = galaxy_generator(1e7/4,    5,  -10.0,  370,  0, n_bodies = 0, radius = 6, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("galactic_center_dynamics_smaller_v1", model, limits = 20, axis_off = False)

In [46]:
galaxy1 = galaxy_generator(1e7,   -7,  -5 ,  0,  0, n_bodies = 0, radius = 6, c_rot = False)
galaxy2 = galaxy_generator(1e7,  7.0, -25.0, 0, 1300, n_bodies = 0, radius = 6, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("galactic_center_dynamics_stationary_v1", model, limits = 30, axis_off = True)



100%|██████████████████████████████████████████████████████████████████████████████| 199/199 [00:00<00:00, 2705.45it/s]


  0%|                                                                                          | 0/200 [00:00<?, ?it/s]

  0%|▍                                                                                 | 1/200 [00:00<00:24,  8.14it/s]

  2%|█▏                                                                                | 3/200 [00:00<00:22,  8.58it/s]

  2%|█▋                                                                                | 4/200 [00:00<00:23,  8.47it/s]

  2%|██                                                                                | 5/200 [00:00<00:22,  8.55it/s]

  3%|██▍                                                                               | 6/200 [00:00<00:22,  8.48it/s]

  4%|██▊                                                                               | 7/200 [00:00<00:23,  8.24it/s]

  4%|███▎                    

## Direct Passage

In [16]:
galaxy1 = galaxy_generator(1e7,   7,   10.0,  -450,  0, n_bodies = 120, radius = 6, c_rot = False)
galaxy2 = galaxy_generator(1e7,  -7,   -10.0,  450,  0, n_bodies =   0, radius = 6, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("direct_passage_one_galaxy_v1", model, limits = 45, axis_off = True)

In [17]:
galaxy1 = galaxy_generator(1e7,   7,   10.0,  -450,  0, n_bodies = 100, radius = 6, c_rot = False)
galaxy2 = galaxy_generator(1e7,  -7,   -10.0,  450,  0, n_bodies = 100, radius = 6, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("direct_passage_two_galaxy_v1", model, limits = 45, axis_off = True)

In [33]:
galaxy1 = galaxy_generator(1e7,   -9,  -5 ,  0,  0, n_bodies = 200, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7,  5, -30.0, 0, 1400, n_bodies = 0, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax, dt, model)
animator("equal_mass_one_galaxy_v1", model, limits = 70, axis_off = True)

100%|████████████████████████████████████████████████████████████████████████████████| 200/200 [00:16<00:00, 11.90it/s]


In [36]:
galaxy1 = galaxy_generator(1e7,   -9,  -5 ,  0,  0, n_bodies = 200, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7/4,  3, -30.0, 0, 1300, n_bodies = 0, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax*2, dt, model)
animator("fourth_mass_one_galaxy_v1", model, limits = 70, axis_off = True)

100%|████████████████████████████████████████████████████████████████████████████████| 400/400 [00:46<00:00,  8.60it/s]


In [37]:
galaxy1 = galaxy_generator(1e7,   -9,  -5 ,  0,  0, n_bodies = 0, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7/4,  3, -30.0, 0, 1300, n_bodies = 200, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax*2, dt, model)
animator("four_times_mass_one_galaxy_v1", model, limits = 70, axis_off = True)

100%|████████████████████████████████████████████████████████████████████████████████| 400/400 [00:51<00:00,  7.72it/s]


In [40]:
galaxy1 = galaxy_generator(1e7,   -9,  -5 ,  0,  0, n_bodies =150, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7/4,  3, -30.0, 0, 1300, n_bodies = 150, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax*2, dt, model)
animator("fourth_mass_two_galaxy_v1", model, limits = 120, axis_off = True)


 33%|██████████████████████████▎                                                     | 131/399 [15:19<31:25,  7.03s/it]


 66%|████████████████████████████████████████████████████▋                           | 263/399 [30:51<16:28,  7.27s/it]


 99%|███████████████████████████████████████████████████████████████████████████████▏| 395/399 [46:19<00:28,  7.01s/it]


100%|████████████████████████████████████████████████████████████████████████████████| 399/399 [46:47<00:00,  7.04s/it]

 32%|█████████████████████████▍                                                      | 127/400 [00:22<00:47,  5.80it/s]


 65%|███████████████████████████████████████████████████▊                            | 259/400 [00:46<00:24,  5.66it/s]


 98%|██████████████████████████████████████████████████████████████████████████████▏ | 391/400 [01:10<00:01,  5.62it/s]


100%|████████████████████████████████████████████████████████████████████████████████| 400/400 [01:11<00:00,  5.58it/s]


In [42]:
galaxy1 = galaxy_generator(1e7,   0,0,0,0, n_bodies =100, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7/2,  17.0, -100.0, 0, 1300, n_bodies = 100, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax*4, dt, model)
animator("half_mass_two_galaxy_v2", model, limits = 160, axis_off = True)



  0%|                                                                                          | 0/799 [00:00<?, ?it/s]

  0%|                                                                                  | 1/799 [00:03<40:35,  3.05s/it]

  0%|▏                                                                                 | 2/799 [00:06<40:43,  3.07s/it]

  0%|▎                                                                                 | 3/799 [00:09<40:21,  3.04s/it]

  1%|▍                                                                                 | 4/799 [00:11<39:12,  2.96s/it]

  1%|▌                                                                                 | 5/799 [00:14<39:20,  2.97s/it]

  1%|▌                                                                                 | 6/799 [00:18<39:58,  3.03s/it]

  1%|▋                                                                                 | 7/799 [00:20<39:36,  3.00s/it]

  1%|▊                        

 16%|████████████▊                                                                   | 128/799 [06:57<35:16,  3.15s/it]

 16%|████████████▉                                                                   | 129/799 [07:01<37:37,  3.37s/it]

 16%|█████████████                                                                   | 130/799 [07:04<36:36,  3.28s/it]

 16%|█████████████                                                                   | 131/799 [07:08<38:22,  3.45s/it]

 17%|█████████████▏                                                                  | 132/799 [07:12<40:17,  3.62s/it]

 17%|█████████████▎                                                                  | 133/799 [07:15<39:11,  3.53s/it]

 17%|█████████████▍                                                                  | 134/799 [07:18<37:36,  3.39s/it]

 17%|█████████████▌                                                                  | 135/799 [07:22<37:00,  3.34s/it]

 17%|█████████████▌             

 32%|█████████████████████████▋                                                      | 256/799 [13:39<29:51,  3.30s/it]

 32%|█████████████████████████▋                                                      | 257/799 [13:43<29:51,  3.31s/it]

 32%|█████████████████████████▊                                                      | 258/799 [13:46<29:28,  3.27s/it]

 32%|█████████████████████████▉                                                      | 259/799 [13:49<28:40,  3.19s/it]

 33%|██████████████████████████                                                      | 260/799 [13:52<27:50,  3.10s/it]

 33%|██████████████████████████▏                                                     | 261/799 [13:55<28:21,  3.16s/it]

 33%|██████████████████████████▏                                                     | 262/799 [13:58<27:51,  3.11s/it]

 33%|██████████████████████████▎                                                     | 263/799 [14:01<27:50,  3.12s/it]

 33%|██████████████████████████▍

 48%|██████████████████████████████████████▍                                         | 384/799 [20:22<20:13,  2.92s/it]

 48%|██████████████████████████████████████▌                                         | 385/799 [20:25<20:22,  2.95s/it]

 48%|██████████████████████████████████████▋                                         | 386/799 [20:28<21:15,  3.09s/it]

 48%|██████████████████████████████████████▋                                         | 387/799 [20:31<21:51,  3.18s/it]

 49%|██████████████████████████████████████▊                                         | 388/799 [20:35<21:55,  3.20s/it]

 49%|██████████████████████████████████████▉                                         | 389/799 [20:38<21:35,  3.16s/it]

 49%|███████████████████████████████████████                                         | 390/799 [20:41<21:38,  3.18s/it]

 49%|███████████████████████████████████████▏                                        | 391/799 [20:44<20:55,  3.08s/it]

 49%|███████████████████████████

 64%|███████████████████████████████████████████████████▎                            | 512/799 [26:59<14:46,  3.09s/it]

 64%|███████████████████████████████████████████████████▎                            | 513/799 [27:02<14:46,  3.10s/it]

 64%|███████████████████████████████████████████████████▍                            | 514/799 [27:05<14:42,  3.10s/it]

 64%|███████████████████████████████████████████████████▌                            | 515/799 [27:08<14:43,  3.11s/it]

 65%|███████████████████████████████████████████████████▋                            | 516/799 [27:11<14:30,  3.08s/it]

 65%|███████████████████████████████████████████████████▊                            | 517/799 [27:14<14:21,  3.06s/it]

 65%|███████████████████████████████████████████████████▊                            | 518/799 [27:17<14:13,  3.04s/it]

 65%|███████████████████████████████████████████████████▉                            | 519/799 [27:20<13:57,  2.99s/it]

 65%|███████████████████████████

...

 28%|██████████████████████▍                                                         | 224/800 [00:48<02:01,  4.74it/s]

 28%|██████████████████████▌                                                         | 225/800 [00:49<02:03,  4.64it/s]

 28%|██████████████████████▌                                                         | 226/800 [00:49<02:04,  4.61it/s]

 28%|██████████████████████▋                                                         | 227/800 [00:49<02:02,  4.68it/s]

 28%|██████████████████████▊                                                         | 228/800 [00:49<02:10,  4.39it/s]

 29%|██████████████████████▉                                                         | 229/800 [00:49<02:07,  4.47it/s]

 29%|███████████████████████                                                         | 230/800 [00:50<02:03,  4.60it/s]

 29%|███████████████████████                                                         | 231/800 [00:50<02:03,  4.63it/s]

 29%|███████████████████████▏   

 44%|███████████████████████████████████▏                                            | 352/800 [01:17<01:39,  4.52it/s]

 44%|███████████████████████████████████▎                                            | 353/800 [01:17<01:43,  4.33it/s]

 44%|███████████████████████████████████▍                                            | 354/800 [01:17<01:43,  4.29it/s]

 44%|███████████████████████████████████▌                                            | 355/800 [01:18<01:44,  4.28it/s]

 44%|███████████████████████████████████▌                                            | 356/800 [01:18<01:42,  4.35it/s]

 45%|███████████████████████████████████▋                                            | 357/800 [01:18<01:40,  4.41it/s]

 45%|███████████████████████████████████▊                                            | 358/800 [01:18<01:39,  4.45it/s]

 45%|███████████████████████████████████▉                                            | 359/800 [01:18<01:37,  4.54it/s]

 45%|███████████████████████████

 60%|████████████████████████████████████████████████                                | 480/800 [01:45<01:08,  4.66it/s]

 60%|████████████████████████████████████████████████                                | 481/800 [01:45<01:08,  4.67it/s]

 60%|████████████████████████████████████████████████▏                               | 482/800 [01:45<01:09,  4.59it/s]

 60%|████████████████████████████████████████████████▎                               | 483/800 [01:45<01:09,  4.58it/s]

 60%|████████████████████████████████████████████████▍                               | 484/800 [01:45<01:07,  4.65it/s]

 61%|████████████████████████████████████████████████▌                               | 485/800 [01:46<01:06,  4.72it/s]

 61%|████████████████████████████████████████████████▌                               | 486/800 [01:46<01:06,  4.76it/s]

 61%|████████████████████████████████████████████████▋                               | 487/800 [01:46<01:06,  4.74it/s]

 61%|███████████████████████████

 76%|████████████████████████████████████████████████████████████▊                   | 608/800 [02:13<00:42,  4.53it/s]

 76%|████████████████████████████████████████████████████████████▉                   | 609/800 [02:13<00:41,  4.60it/s]

 76%|█████████████████████████████████████████████████████████████                   | 610/800 [02:13<00:40,  4.71it/s]

 76%|█████████████████████████████████████████████████████████████                   | 611/800 [02:13<00:39,  4.74it/s]

 76%|█████████████████████████████████████████████████████████████▏                  | 612/800 [02:13<00:39,  4.80it/s]

 77%|█████████████████████████████████████████████████████████████▎                  | 613/800 [02:14<00:38,  4.82it/s]

 77%|█████████████████████████████████████████████████████████████▍                  | 614/800 [02:14<00:39,  4.70it/s]

 77%|█████████████████████████████████████████████████████████████▌                  | 615/800 [02:14<00:39,  4.63it/s]

 77%|███████████████████████████

 92%|█████████████████████████████████████████████████████████████████████████▌      | 736/800 [02:41<00:18,  3.40it/s]

 92%|█████████████████████████████████████████████████████████████████████████▋      | 737/800 [02:41<00:18,  3.43it/s]

 92%|█████████████████████████████████████████████████████████████████████████▊      | 738/800 [02:42<00:18,  3.37it/s]

 92%|█████████████████████████████████████████████████████████████████████████▉      | 739/800 [02:42<00:17,  3.49it/s]

 92%|██████████████████████████████████████████████████████████████████████████      | 740/800 [02:42<00:16,  3.63it/s]

 93%|██████████████████████████████████████████████████████████████████████████      | 741/800 [02:42<00:15,  3.75it/s]

 93%|██████████████████████████████████████████████████████████████████████████▏     | 742/800 [02:43<00:15,  3.81it/s]

 93%|██████████████████████████████████████████████████████████████████████████▎     | 743/800 [02:43<00:14,  3.82it/s]

 93%|███████████████████████████

In [10]:
galaxy1 = galaxy_generator(1e7,   0,0,0,0, n_bodies = 200, radius = 10, c_rot = False)
galaxy2 = galaxy_generator(1e7/2,  17.0, -100.0, 0, 1300, n_bodies = 200, radius = 10, c_rot = False)
model = []
model.extend(galaxy1)
model.extend(galaxy2)
orbit_dynamics(t, tMax*4, dt, model)
animator("half_mass_two_galaxy_v2", model, limits = 160, axis_off = True)

100%|████████████████████████████████████████████████████████████████████████████████| 800/800 [04:23<00:00,  3.04it/s]
